# Get Chick-fil-A locations

#### Load Python tools and Jupyter config

In [1]:
import re
import json
import random
import requests
import numpy as np
import pandas as pd
import jupyter_black
import altair as alt
from time import sleep
import geopandas as gpd
from random import randint
from bs4 import BeautifulSoup
from vega_datasets import data
from tqdm.notebook import tqdm, trange

In [2]:
pd.options.display.max_rows = 1000
pd.options.display.max_columns = 1000
pd.options.display.max_colwidth = None

In [3]:
place = "chick-fil-a"
place_formal = "Chick-fil-A"
color = "#E51636"

---

## ZIP Codes

In [4]:
zips = pd.read_csv(
    "../_reference/data/usa-zips-wealth.csv"
).sort_values("totpop_cy", ascending=False)

In [5]:
# zips_sample = zips.sample(3000).sort_values("totpop_cy", ascending=False)
# zips_list = zips_sample["id"].to_list()
zips_list = zips["id"].head(1000).to_list()

#### Get locations

In [6]:
cookies = {
    "__cf_bm": "fNCpunN8rEnZPNiObTAg1B46cqeO8IxjI9ebasrVx6s-1657977733-0-ASjZhBbj06P+ztVnJiMdiyXAqDfdj2fSG1CUFApZExMjUumrRKbmhz4cCZAaBUKqdKQGLVmzm9oNeehH30lfjqs=",
}

headers = {
    "authority": "locator.chick-fil-a.com.yext-cdn.com",
    "accept": "application/json",
    "accept-language": "en-US,en;q=0.9,es;q=0.8",
    "referer": "https://locator.chick-fil-a.com.yext-cdn.com/search?q=30354&per=10",
    "sec-ch-ua": '".Not/A)Brand";v="99", "Google Chrome";v="103", "Chromium";v="103"',
    "sec-ch-ua-mobile": "?0",
    "sec-ch-ua-platform": '"macOS"',
    "sec-fetch-dest": "empty",
    "sec-fetch-mode": "cors",
    "sec-fetch-site": "same-origin",
    "user-agent": "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/103.0.0.0 Safari/537.36",
}

In [7]:
responses = []

for z in tqdm(zips_list):
    params = {
        "q": z,
        "per": "50",
    }

    response = requests.get(
        "https://locator.chick-fil-a.com.yext-cdn.com/search",
        params=params,
        cookies=cookies,
        headers=headers,
    )
    responses.append(response.json())
    # sleep(randint(1,2))

  0%|          | 0/1000 [00:00<?, ?it/s]

In [8]:
dicts = []

for r in responses:
    for p in r["response"]["entities"]:
        dicts.append(p["profile"])

In [9]:
src = pd.DataFrame(dicts)

In [10]:
src[
    [
        "city",
        "countryCode",
        "extraDescription",
        "line1",
        "line2",
        "line3",
        "postalCode",
        "region",
        "sublocality",
    ]
] = pd.json_normalize(src["address"])

In [11]:
src_slim = src[
    [
        "c_driveThru",
        "c_locationFormat",
        "c_locationName",
        "c_mall",
        "c_marketName",
        "c_openDate",
        "c_operatorName",
        "c_playground",
        "c_projectedOpenDate",
        "c_status",
        "geocodedCoordinate",
        "timezone",
        "websiteUrl",
        "city",
        "countryCode",
        "line1",
        "postalCode",
        "region",
    ]
].copy()

In [12]:
src_slim.columns = src_slim.columns.str.lower().str.replace("c_", "", regex=False)

In [13]:
src_slim[["open_day", "open_month", "open_year"]] = pd.json_normalize(
    src_slim["opendate"]
)

In [14]:
src_slim[["latitude", "longitude"]] = pd.json_normalize(src_slim["geocodedcoordinate"])

In [15]:
df = src_slim.drop(["geocodedcoordinate", "opendate"], axis=1).rename(
    columns={
        "operatorname": "operator",
        "websiteurl": "url",
        "projectedopendate": "other_date",
        "line1": "address",
        "postalcode": "zip",
        "mall": "in_mall",
        "locationformat": "format",
        'region':'state',
    }
)[
    [
        "locationname",
        "marketname",
        "city",
        "countrycode",
        "address",
        "zip",
        "state",
        "latitude",
        "longitude",
        "operator",
        "status",
        "timezone",
        "url",
        "open_day",
        "open_month",
        "open_year",
        "other_date",
        "playground",
        "drivethru",
        "format",
        "in_mall",
    ]
].drop_duplicates().copy()

----

#### How many?

In [16]:
len(df)

2896

In [17]:
formats = ["Stand Alone", "In-Line", "Food Court"]

In [18]:
df_open = df[(df["status"] == "OPEN") & (df["state"] != "AK") & (df["latitude"] > 0)].copy()
df_open_clean = df[df["format"].isin(formats)]

In [19]:
df_open.head()

locationname   marketname     city countrycode                address  \
0  Morton Ranch  Houston, TX     Katy          US    2826 W Grand Pkwy N   
1    Mason Road  Houston, TX     Katy          US         369 S Mason Rd   
3    Katy Green  Houston, TX  Houston          US         19303 Katy Fwy   
4    Katy Mills  Houston, TX     Katy          US       25601 Nelson Way   
5   Cinco Ranch  Houston, TX     Katy          US  23860 Westheimer Pkwy   

     zip state   latitude  longitude                  operator status  \
0  77449    TX  29.814042 -95.772170               Amanda Baca   OPEN   
1  77450    TX  29.780570 -95.751140               Rusty Wylie   OPEN   
3  77094    TX  29.784326 -95.706516               Rusty Wylie   OPEN   
4  77494    TX  29.774121 -95.819225  Cavin, Cynthia (Cynthia)   OPEN   
5  77494    TX  29.735510 -95.778000     Wylie, Martin (Rusty)   OPEN   

          timezone  \
0  America/Chicago   
1  America/Chicago   
3  America/Chicago   
4  America/Chicago   
5  America/Chicago   

                                                                                     url  \
0  https://www.chick-fil-a.com/locations/tx/morton-ranch?utm_source=yext&utm_medium=link   
1    https://www.chick-fil-a.com/locations/tx/mason-road?utm_source=yext&utm_medium=link   
3    https://www.chick-fil-a.com/locations/tx/katy-green?utm_source=yext&utm_medium=link   
4    https://www.chick-fil-a.com/locations/tx/katy-mills?utm_source=yext&utm_medium=link   
5   https://www.chick-fil-a.com/locations/tx/cinco-ranch?utm_source=yext&utm_medium=link   

   open_day  open_month  open_year  other_date playground drivethru  \
0      30.0        11.0     2017.0  2017-11-30   interior      True   
1      14.0         9.0     1995.0  1995-09-14   interior      True   
3      11.0         6.0     2015.0  2015-06-11   interior      True   
4      26.0         4.0     2012.0  2011-12-08   interior      True   
5       2.0         6.0     2005.0  2005-06-02       none      True   

        format in_mall  
0  Stand Alone   False  
1  Stand Alone   False  
3  Stand Alone   False  
4  Stand Alone   False  
5  Stand Alone   False

---

## Geography

#### Make it a geodataframe

In [20]:
df_geo = df.copy()

In [21]:
gdf = gpd.GeoDataFrame(
    df_geo, geometry=gpd.points_from_xy(df_geo.longitude, df_geo.latitude)
)

In [22]:
locations_gdf = gdf.set_crs("EPSG:4326").copy()

---

## Maps

#### US states background

In [23]:
background = (
    alt.Chart(alt.topo_feature(data.us_10m.url, feature="states"))
    .mark_geoshape(fill="#e9e9e9", stroke="white")
    .properties(width=800, height=500, title=f"{place_formal} locations")
    .project("albersUsa")
)

#### Location points map

In [24]:
points = (
    alt.Chart(gdf)
    .mark_circle(size=10, color=color)
    .encode(
        longitude="longitude:Q",
        latitude="latitude:Q",
    )
)

point_map = background + points
point_map.configure_view(stroke=None)

alt.LayerChart(...)

#### Location proportional symbols map

In [25]:
symbols = (
    alt.Chart(gdf)
    .transform_aggregate(
        latitude="mean(latitude)",
        longitude="mean(longitude)",
        count="count()",
        groupby=["state"],
    )
    .mark_circle()
    .encode(
        longitude="longitude:Q",
        latitude="latitude:Q",
        size=alt.Size("count:Q", title="Count by state"),
        color=alt.value(color),
        tooltip=["state:N", "count:Q"],
    )
    .properties(
        title=f"Number of {place_formal} in US, by average lon/lat of locations"
    )
)

symbol_map = background + symbols
symbol_map.configure_view(stroke=None)

alt.LayerChart(...)

---

## Exports

#### JSON

In [26]:
df.to_json(
    f"data/processed/{place.lower().replace(' ', '_')}_locations.json",
    indent=4,
    orient="records",
)

#### CSV

In [27]:
df.to_csv(
    f"data/processed/{place.lower().replace(' ', '_')}_locations.csv", index=False
)

#### GeoJSON

In [28]:
locations_gdf.to_file(
    f"data/processed/{place.lower().replace(' ', '_')}_locations.geojson",
    driver="GeoJSON",
)